# Scraping Article URLs

1. Clean up what we actually scrape from the website: take out 
* related links e.g., 'RELATED:'
* advertisements e.g., 'FEATURED:'
* 'SPECIAL REPORT:'
can take all paragraphs in the content column, then remove the columns that were in the featured / related elements from the paragraphs.\
can just leave in "Editor's note" paragraphs because there's no way to exclude from the scraping, unless we hard-code a rule to leave out paragraphs that start with "Editor's note".

2. Clean up how we record the articles. There should be clear separation of paragraphs... probably one paragraph per cell.

3. final result should store:
* url
* article title
* article date
* every paragraph in a separate row
* article tags

In [1]:
import pandas as pd
import numpy as np
import os
import time
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from bs4 import BeautifulSoup as bs
import urllib.request 
from bs4 import NavigableString
from urllib.request import urlopen
from selenium.common.exceptions import ElementClickInterceptedException, StaleElementReferenceException
from selenium.webdriver.chrome.options import Options
import pprint
article_list=list(pd.read_csv("working_list.csv")['article'])
problematic_list=list(pd.read_csv("problems.csv")['0'])
date_list=list(pd.read_csv("working_list.csv")['date'])
raw_links=list(pd.read_csv("ref.csv")['raw_links'])


In [4]:
options = Options()
options.page_load_strategy = 'none'
driver = webdriver.Chrome(options=options)

# link = driver.find_element_by_class_name("load-more")


In [3]:
raw_headlines=[]
raw_links=[]
raw_dates=[]
domains=[
    'vaccines',
    'asia',
    'keyword/cell-gene-therapy',
    'keyword/drug-delivery',
    'facilities'
]
for domain in domains:
    driver.get(f"https://www.fiercepharma.com/{domain}")
    time.sleep(3)
    click=0
    for click in range(30):
        try:
            # time.sleep(2) #for page to load
            # link.click()
            time.sleep(2) #for page to load
            # driver.execute_script("window.scrollTo(500, document.body.scrollHeight);")
            # time.sleep() #for page to load
            # link = driver.find_element(By.XPATH,"//a[@title='Load more items']")
            link = driver.find_element(By.XPATH,"//div/span[@class='extended-load d-inline-block']")
            link.click()
            # time.sleep(2)
            click+=1
        except ElementClickInterceptedException:
            click+=0
        except StaleElementReferenceException:
            click+=0
        except:
            click+=1
    dates = driver.find_elements(By.CLASS_NAME, "date.d-inline-block")
    headlines1 = driver.find_elements(By.XPATH,"//h3[@class='element-title large']//a")
    headlines2 = driver.find_elements(By.XPATH,"//h3[@class='element-title xsmall']//a")
    headlines3 = driver.find_elements(By.XPATH,"//div[@class='element-title small']//a")
    for headline in headlines1:
        raw_links.append(headline.get_attribute("href"))
        raw_headlines.append(headline.text)
    for headline in headlines2:
        raw_links.append(headline.get_attribute("href"))
        raw_headlines.append(headline.text)
    for headline in headlines3:
        raw_links.append(headline.get_attribute("href"))
        raw_headlines.append(headline.text)
    for date in dates:
        raw_dates.append(date.text)
print(len(raw_headlines))
print(len(raw_dates))
print(len(raw_links))

1079
1067
1079


In [74]:
# test_links=test_links.split(',')
test_links[0]=test_links[0].replace('[','')
raw_links=[i.replace("'",'') for i in test_links]
raw_links

['https://www.fiercepharma.com/pharma/moderna-looks-scale-back-manufacturing-covid-booster-cope-falling-demand-reuters',
 ' https://www.fiercepharma.com/pharma/cdc-starts-wild-mild-campaign-reverse-falling-flu-vaccine-use-key-groups',
 ' https://www.fiercepharma.com/manufacturing/japan-awards-115m-arcturus-jv-boost-mrna-manufacturing',
 ' https://www.fiercepharma.com/marketing/biontech-and-x-warned-pr-body-trying-duck-covid-19-vaccine-debate',
 ' https://www.fiercepharma.com/manufacturing/astrazeneca-commits-mrna-signs-vaccine-manufacturing-deal-chinas-cansino',
 ' https://www.fiercepharma.com/pharma/echoing-pfizer-biontech-carefully-watching-cost-amid-declining-covid-vaccine-sales',
 ' https://www.fiercepharma.com/pharma/takeda-yanks-fda-application-dengue-vaccine-citing-data-collection-disagreement',
 ' https://www.fiercepharma.com/manufacturing/novavax-receive-350m-canada-canceled-covid-vaccine-orders',
 ' https://www.fiercepharma.com/marketing/fingerprint-spying-growing-vaccine-mar

# Regular Code

In [5]:
# article_list=pd.read_csv("working_list.csv")['article'][0]
# problematic_list=pd.read_csv("problems.csv")['problems'][0]
# date_list=pd.read_csv("working_list.csv")['date'][0]
# raw_links=pd.read_csv("working_list.csv")['raw_links'][0]
problematic_list=[]
successful_list=[]
i=1
for url in raw_links:
        driver.get(url)
        try:
                time.sleep(4)
                # driver.execute_script("window.stop();")
                # paragraphs=driver.find_elements(By.TAG_NAME,"p")
                # paragraphs=driver.find_elements(By.XPATH,"//div[@class='col content']//p")
                url_paragraphs=[]
                url_paragraphs.extend([i.text.strip() for i in driver.find_elements(By.XPATH,"//div[@class='col content']//p") if len(i.text.strip()) != 0])
                for paragraph in url_paragraphs:
                        if paragraph[:8]=='RELATED:': url_paragraphs.remove(paragraph)
                        elif paragraph[:9]=='FEATURED:': url_paragraphs.remove(paragraph)
                        elif paragraph[:15]=='SPECIAL REPORT:': url_paragraphs.remove(paragraph)
                tags = [tag.text.strip() for tag in driver.find_elements(By.XPATH,"//div[@id='article-tags-bottom-row']//a")]
                date = driver.find_elements(By.XPATH,"//span[@class='date d-block d-md-inline-block']")[0].text
                successful_list.append([url,date,url_paragraphs,tags])
                print(f'done with {i}')
                # problematic_list.pop(url)
        except:
                problematic_list.append(url)
                print(f'problem with {i}')
        i+=1

done with 1
done with 2
done with 3
done with 4
done with 5
done with 6
done with 7
done with 8
done with 9
done with 10
done with 11
done with 12
done with 13
done with 14
done with 15
done with 16
done with 17
done with 18
done with 19
done with 20
done with 21
done with 22
done with 23
done with 24
done with 25
done with 26
done with 27
done with 28
done with 29
done with 30
done with 31
done with 32
done with 33
done with 34
done with 35
done with 36
done with 37
done with 38
done with 39
done with 40
done with 41
done with 42
done with 43
done with 44
done with 45
done with 46
done with 47
done with 48
done with 49
done with 50
done with 51
done with 52
done with 53
done with 54
done with 55
done with 56
done with 57
done with 58
done with 59
done with 60
done with 61
done with 62
done with 63
done with 64
done with 65
done with 66
done with 67
done with 68
done with 69
done with 70
done with 71
done with 72
done with 73
done with 74
done with 75
done with 76
done with 77
done wit

In [38]:
df=pd.DataFrame(columns=['url','date','paragraph','tags'])
for item in successful_list:
    content=[]
    for paragraph in item[2]:
        content.append(paragraph)
    temp=pd.DataFrame(data={'paragraph':content})
    temp['url']=item[0]
    temp['date']=item[1]
    temp['tags']=[item[3] for i in temp.index]
    temp=temp[df.columns]
    df=pd.concat([df,temp])
df

url                  date  \
0   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
1   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
2   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
3   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
4   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
..                                                ...                   ...   
10   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   
11   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   
12   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   
13   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   
14   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   

                                            paragraph  \
0   While the FDA and the Centers for Disease Cont...   
1   Moderna is speaking with its manufacturing par...   
2   “Over the past couple of years, we’ve been in ...   
3   The discussions are with vial fillers, accordi...   
4   Separately, Lonza helps manufacture the drug s...   
..                                                ...   
10  "Looking ahead, the Prescription Drug User Fee...   
11  Meanwhile, the FDA on Monday said it was resum...   
12  “In addition to the resumption of planning and...   
13  The FDA added it would move forward with previ...   
14  Editor's note: This story has been updated wit...   

                                                 tags  
0   [Moderna, COVID-19, Spikevax, vaccine manufact...  
1   [Moderna, COVID-19, Spikevax, vaccine manufact...  
2   [Moderna, COVID-19, Spikevax, vaccine manufact...  
3   [Moderna, COVID-19, Spikevax, vaccine manufact...  
4   [Moderna, COVID-19, Spikevax, vaccine manufact...  
..                                                ...  
10  [coronavirus, COVID-19, facilities, FDA inspec...  
11  [coronavirus, COVID-19, facilities, FDA inspec...  
12  [coronavirus, COVID-19, facilities, FDA inspec...  
13  [coronavirus, COVID-19, facilities, FDA inspec...  
14  [coronavirus, COVID-19, facilities, FDA inspec...  

[12010 rows x 4 columns]

In [41]:
#get count of all tags across all time 
tag_dict={}
for tags in df['tags']:
    for tag in tags:
        try: tag_dict[f'{tag}']+=1
        except: tag_dict[f'{tag}']=1
tag_dict

{'Moderna': 1695,
 'COVID-19': 4314,
 'Spikevax': 114,
 'vaccine manufacturing': 1272,
 'Thermo Fisher': 39,
 'Catalent': 189,
 'Sanofi': 971,
 'CDMO': 601,
 'aseptic filling': 20,
 'contract manufacturing': 110,
 'Manufacturing': 1440,
 'Vaccines': 3508,
 'Fierce Pharma': 10090,
 'CDC': 45,
 'flu vaccine': 292,
 'awareness campaigns': 111,
 'Campaigns': 6,
 'Pharma': 4444,
 'Marketing': 707,
 'Arcturus Therapeutics': 54,
 'mRNA': 268,
 'CSL': 24,
 'Arcturus': 24,
 'Seqirus': 222,
 'Meiji Seika Pharma': 38,
 'Japan': 271,
 'Financials': 291,
 'Asia': 1388,
 'BioNTech': 1079,
 'Germany': 86,
 'X': 11,
 'Twitter': 38,
 'AstraZeneca': 1412,
 'CanSino Biologics': 61,
 'China': 769,
 'Tianjin CanSino': 61,
 'Deals': 249,
 'Comirnaty': 224,
 'Earnings': 423,
 'Pfizer': 2436,
 'Takeda': 934,
 'Qdenga': 92,
 'U.S. FDA': 1445,
 'Dengue fever': 282,
 'vaccine development': 1700,
 'Novavax': 603,
 'Canada': 95,
 'market access': 6,
 'mergers and acquisitions': 297,
 'vaccines': 50,
 'Fluzone': 43

In [65]:
expanded_df=df.copy()
# merge related tags together
grouped_tags={
    '"Alzheimers disease"': '"Alzheimers"',
    '"Parkinsons disease"': '"Parkinsons drug"',
    'Arcturus':'Arcturus Therapeutics',
    'BD':'Becton Dickinson',
    'Aspen':'Aspen Pharmacare',
    'Alnylam':'Alnylam Pharmaceuticals',
    'acute myeloid leukemia':'acute myeloid leukemia (AML)',
    'biosimilar':'biosimilars',
    'Cell & Gene Therapy':'cell therapy',
    'Cell & Gene Therapy':'gene therapy',
    'funding':'Fundraising',
    'JAK inhibitor':'JAK inhibitors',
    'Sun Pharmaceutical':'Sun Pharmaceuticals',
    'Supply Chain':'Supply Chains',
    'Teva Pharmaceutical':'Teva Pharmaceuticals',
    'Takeda':'Takeda Pharmaceutical',
    'Thermo Fisher':'Thermo Fisher Scientific',
    'U.K.':'United Kingdom',
    'Venture Capital':'venture capital (VC)',
    'Walter Reed':'Walter Reed Army Institute of Research',
    'Duchenne muscular dystrophy':'Duchenne muscular dystrophy (DMD)',
    'CRISPR':'CRISPR-Cas9',
    'Manufacturing deal':'Manufacturing deals',
    'FDA approval':'FDA approvals',
    'antibody drug conjugates':'antibody-drug conjugates',
    'ADCs':'antibody drug conjugates',
    'Vaccine':'Vaccines',
    'partnership':'partnerships',
    'coronavirus':'COVID-19'
}
for i in range(len(expanded_df['tags'])):
    temp_list=expanded_df['tags'].iloc[i]
    for tag in expanded_df['tags'].iloc[i]:
        if tag in grouped_tags.keys():
            temp_list[temp_list.index(tag)]=grouped_tags[tag]
    expanded_df['tags'].iloc[i]=list(set(temp_list))
tag_dict={}
for tags in expanded_df['tags']:
    for tag in tags:
        try: tag_dict[f'{tag}']+=1
        except: tag_dict[f'{tag}']=1
for tag in list(tag_dict.keys()):
    result=[]
    for tag_list in expanded_df['tags']:
        if tag in tag_list: result.append(1)
        else: result.append(0)
    expanded_df[f'{tag}']=result 
expanded_df

/var/folders/2q/m02shclj04v8g_2vqn0pwr3c0000gp/T/ipykernel_55895/1723125212.py:50: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  expanded_df[f'{tag}']=result
/var/folders/2q/m02shclj04v8g_2vqn0pwr3c0000gp/T/ipykernel_55895/1723125212.py:50: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  expanded_df[f'{tag}']=result
/var/folders/2q/m02shclj04v8g_2vqn0pwr3c0000gp/T/ipykernel_55895/1723125212.py:50: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor pe

url                  date  \
0   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
1   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
2   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
3   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
4   https://www.fiercepharma.com/pharma/moderna-lo...  Sep 13, 2023 10:25am   
..                                                ...                   ...   
10   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   
11   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   
12   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   
13   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   
14   https://www.fiercepharma.com/pharma/fda-must-...    Feb 7, 2022 2:46pm   

                                            paragraph  \
0   While the FDA and the Centers for Disease Cont...   
1   Moderna is speaking with its manufacturing par...   
2   “Over the past couple of years, we’ve been in ...   
3   The discussions are with vial fillers, accordi...   
4   Separately, Lonza helps manufacture the drug s...   
..                                                ...   
10  "Looking ahead, the Prescription Drug User Fee...   
11  Meanwhile, the FDA on Monday said it was resum...   
12  “In addition to the resumption of planning and...   
13  The FDA added it would move forward with previ...   
14  Editor's note: This story has been updated wit...   

                                                 tags  Spikevax  Sanofi  \
0   [Spikevax, Sanofi, contract manufacturing, Mod...         1       1   
1   [Spikevax, Sanofi, contract manufacturing, Mod...         1       1   
2   [Spikevax, Sanofi, contract manufacturing, Mod...         1       1   
3   [Spikevax, Sanofi, contract manufacturing, Mod...         1       1   
4   [Spikevax, Sanofi, contract manufacturing, Mod...         1       1   
..                                                ...       ...     ...   
10  [India, China, Facilities, COVID-19, FDA inspe...         0       0   
11  [India, China, Facilities, COVID-19, FDA inspe...         0       0   
12  [India, China, Facilities, COVID-19, FDA inspe...         0       0   
13  [India, China, Facilities, COVID-19, FDA inspe...         0       0   
14  [India, China, Facilities, COVID-19, FDA inspe...         0       0   

    contract manufacturing  Moderna  Catalent  CDMO  ...  plant closure  \
0                        1        1         1     1  ...              0   
1                        1        1         1     1  ...              0   
2                        1        1         1     1  ...              0   
3                        1        1         1     1  ...              0   
4                        1        1         1     1  ...              0   
..                     ...      ...       ...   ...  ...            ...   
10                       0        0         0     0  ...              0   
11                       0        0         0     0  ...              0   
12                       0        0         0     0  ...              0   
13                       0        0         0     0  ...              0   
14                       0        0         0     0  ...              0   

    FDA recall  Wockhardt  Macleods  Ncardia  Trodelvy  \
0            0          0         0        0         0   
1            0          0         0        0         0   
2            0          0         0        0         0   
3            0          0         0        0         0   
4            0          0         0        0         0   
..         ...        ...       ...      ...       ...   
10           0          0         0        0         0   
11           0          0         0        0         0   
12           0          0         0        0         0   
13           0          0         

In [72]:
for_saving=expanded_df.copy()
for i in range(len(for_saving)):
    for_saving['tags'].iloc[i]=",".join(for_saving['tags'].iloc[i])
for_saving.to_csv("all articles and tags.csv")

/var/folders/2q/m02shclj04v8g_2vqn0pwr3c0000gp/T/ipykernel_55895/3006461555.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  for_saving['tags'].iloc[i]=",".join(for_saving['tags'].iloc[i])
/var/folders/2q/m02shclj04v8g_2vqn0pwr3c0000gp/T/ipykernel_55895/3006461555.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  for_saving['tags'].iloc[i]=",".join(for_saving['tags'].iloc[i])
/var/folders/2q/m02shclj04v8g_2vqn0pwr3c0000gp/T/ipykernel_55895/3006461555.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pand

# Annex

In [20]:
# problematic list dedicated code

options = Options()
options.page_load_strategy = 'none'
driver = webdriver.Chrome(options=options)

# link = driver.find_element_by_class_name("load-more")

# article_list=pd.read_csv("working_list.csv")['article'][0]
# problematic_list=pd.read_csv("problems.csv")['problems'][0]
# date_list=pd.read_csv("working_list.csv")['date'][0]
# raw_links=pd.read_csv("working_list.csv")['raw_links'][0]
# article_list=[]
# problematic_list=[]
# date_list=[]
i=1
article_list=[]
test_problems=problematic_list[0:2]
for url in test_problems:
# for url in raw_links[len(article_list)+len(problematic_list):]:
        driver.get(url)
        time.sleep(15)
        driver.execute_script("window.stop();")
        # paragraphs=driver.find_elements(By.TAG_NAME,"p")
        # paragraphs=driver.find_elements(By.XPATH,"//div[@class='col content']//p")
        url_paragraphs=[]
        url_paragraphs.extend([i.text for i in driver.find_elements(By.XPATH,"//div[@class='col content']//p")])
        # for paragraph in paragraphs:
        #         url_paragraphs.append(paragraph.text)
        date_list.append(driver.find_elements(By.XPATH,"//span[@class='date d-block d-md-inline-block']")[0].text)
        article_list.append(url_paragraphs)
        problematic_list.pop(problematic_list.index(url))
        print(f"done with {i}")
        i+=1

done with 1
done with 2


In [24]:
article_list

["Like many CDMOs these days, Switzerland's Celonic aims to make a big splash in cell and gene therapy—and it's picked up space at an emerging Novartis life sciences hub to take that work to the next level. ",
 'Celonic sewed up a long-term lease for production and office space in the WST-222 building of Novartis’ hub-to-be in Stein, Switzerland, dubbed Life Science Park Rheintal. The company will use the 91,500-square-foot location to set up production capacity for cell and gene therapies, next-generation vaccines and “innovative biopharmaceuticals.”',
 '',
 'Celonic is adding up to 20 clean room suites, plus offices and laboratories for process development, method development and quality control for clients from early-stage work to market. It will also sign around 250 new employees to staff the site, which should be ready for production by the second quarter of 2022.',
 '',
 '',
 '',
 '',
 'RELATED: Cognate beefs up cell, gene therapy manufacturing with new plants in U.S., EU',
 'The

In [14]:
import pandas as pd
working_df=pd.DataFrame(data={'article':article_list,'date':date_list})
working_df.to_csv("working_list.csv")
# ref=pd.DataFrame(data={'headlines':raw_headlines,'raw_links':raw_links})
# ref.to_csv("ref.csv")
problems=pd.DataFrame(problematic_list)
problems.to_csv("problems.csv")

In [16]:
working_df

article                  date
0     ['While the FDA and the Centers for Disease Co...  Sep 13, 2023 10:25am
1     ['The Centers for Disease Control and Preventi...  Sep 12, 2023 10:46am
2     ["Right after Daiichi Sankyo picked up Japan's...  Aug 14, 2023 11:58am
3     ['The self-regulatory body of the German commu...  Aug 10, 2023 02:18am
4     ['Despite a Moderna partnership that turned so...   Aug 9, 2023 11:28am
...                                                 ...                   ...
1054  [Almost 90% of pharmaceutical companies see sm...  May 11, 2021 06:40am
1055  [Alexion Pharmaceuticals has wasted no time co...  Oct 16, 2020 12:05pm
1056  [The FDA just doled out the first nod under a ...   Oct 1, 2018 12:20pm
1057  [Ten23 health, a CDMO that launched just six m...  Mar 28, 2022 09:30am
1058  [The FDA is pushing back the approval of GC Ph...   Mar 1, 2022 09:54am

[1059 rows x 2 columns]

In [25]:
working_df.rename(columns={'date':'datetime'},inplace=True)
working_df['date']=pd.to_datetime(working_df['datetime'], format='mixed').dt.date

article              datetime  \
0     ['While the FDA and the Centers for Disease Co...  Sep 13, 2023 10:25am   
1     ['The Centers for Disease Control and Preventi...  Sep 12, 2023 10:46am   
2     ["Right after Daiichi Sankyo picked up Japan's...  Aug 14, 2023 11:58am   
3     ['The self-regulatory body of the German commu...  Aug 10, 2023 02:18am   
4     ['Despite a Moderna partnership that turned so...   Aug 9, 2023 11:28am   
...                                                 ...                   ...   
1054  [Almost 90% of pharmaceutical companies see sm...  May 11, 2021 06:40am   
1055  [Alexion Pharmaceuticals has wasted no time co...  Oct 16, 2020 12:05pm   
1056  [The FDA just doled out the first nod under a ...   Oct 1, 2018 12:20pm   
1057  [Ten23 health, a CDMO that launched just six m...  Mar 28, 2022 09:30am   
1058  [The FDA is pushing back the approval of GC Ph...   Mar 1, 2022 09:54am   

            date  
0     2023-09-13  
1     2023-09-12  
2     2023-08-14  
3     2023-08-10  
4     2023-08-09  
...          ...  
1054  2021-05-11  
1055  2020-10-16  
1056  2018-10-01  
1057  2022-03-28  
1058  2022-03-01  

[1059 rows x 3 columns]

In [27]:
working_df=working_df.sort_values(by="date")
working_df.to_csv("all_articles.csv")

In [27]:
working_df=pd.DataFrame(data={'article':article_list})
working_df.to_csv("test.csv")
working_df['article'][0]

['For developers of cell and gene therapies, the path to market often seems to be marred with potholes. The FDA rejected BioMarin Pharmaceutical’s gene therapy to treat hemophilia A in 2020, citing the need for more durability data and sending the company’s shares down more than 20% in a day. In November of this year, the FDA delayed a much-anticipated decision on multiple myeloma CAR-T candidate cilta-cel from Legend Biotech and Johnson & Johnson, causing Legend’s stock to fall nearly 8%.',
 'Now, those companies are preparing for the FDA to finally hand down its rulings—and they’re making those preparations optimistically. Biomarin expects to submit new data on its gene therapy, Roctavian, to the FDA in 2022, setting up a potential approval by the end of the year. And, at this year’s American Society of Hematology (ASH) meeting, Legend and J&J rolled out such positive survival data from their cilta-cel trial that some analysts suggested—if it’s approved in February as expected—it cou

In [33]:
result=pd.read_csv("test.csv")
pp.pprint(result['article'][0])

("['For developers of cell and gene therapies, the path to market often seems "
 'to be marred with potholes. The FDA rejected BioMarin Pharmaceutical’s gene '
 'therapy to treat hemophilia A in 2020, citing the need for more durability '
 'data and sending the company’s shares down more than 20% in a day. In '
 'November of this year, the FDA delayed a much-anticipated decision on '
 'multiple myeloma CAR-T candidate cilta-cel from Legend Biotech and Johnson & '
 "Johnson, causing Legend’s stock to fall nearly 8%.', 'Now, those companies "
 'are preparing for the FDA to finally hand down its rulings—and they’re '
 'making those preparations optimistically. Biomarin expects to submit new '
 'data on its gene therapy, Roctavian, to the FDA in 2022, setting up a '
 'potential approval by the end of the year. And, at this year’s American '
 'Society of Hematology (ASH) meeting, Legend and J&J rolled out such positive '
 'survival data from their cilta-cel trial that some analysts suggeste